### This Notebook will use a formula to determine the reccomended KVA for a transformer when it is replaced
The formula uses customer count and customer consumption history downsteam of each transformer. When Electric Trouble Crews replace a transformer the reccomended size will available when an Engineer is not (for example after hours or weekends). This will help ensure the right size transformer is used based on consumption history, and not merley just areplacement that could be under-sized or over-sized.
The second half of the Notebook explores the electric consumption data with a [SpatialDataFrame](https://esri.github.io/arcgis-python-api/apidoc/html/arcgis.features.toc.html?highlight=spatialdataframe#spatialdataframe) using the customers table modifed in the first half.

In [1]:
import arcpy
#import numpy
#import pandas as pd
from datetime import datetime

In [2]:
gdb = r"C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb"
txSource = r"C:\GISData\Data\Snapshot\mxElectric.geodatabase\Electric\main.eTransformerBank"
txDest = r"C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank"
svcPntDest = r"C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eServicePoint"
custAcctSource = r"C:\GISData\Data\Snapshot\mxElectric.geodatabase\main.eCUSTOMERACCOUNT"
custAcctDest = r"C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\eCUSTOMERACCOUNT"
txAddFlds = ["kWDSum","CF","kWDSumXCF"]
txFlds = ["GLOBALID","kWDSum","CF","kWDSumXCF","DEVICEID","FEEDERID","FEEDERID2","INSTALLATIONDATE","PHASEDESIGNATION","SUBTYPE","RATEDKVA_A","RATEDKVA_B","RATEDKVA_C","CUSTOMERCOUNT","STRUCTUREID","FACILITYID","AVGCUSTOMERCONSUMPTION_A","AVGCUSTOMERCONSUMPTION_B","AVGCUSTOMERCONSUMPTION_C","MAXCUSTOMERCONSUMPTION_A","MAXCUSTOMERCONSUMPTION_B","MAXCUSTOMERCONSUMPTION_C","PURPOSE","STREETADDRESS","eSupportStructure_GlobalID","eSurfaceStructure_GlobalID"]
svcPntFlds = ["GLOBALID","eTransformerBank_GLOBALID","FEEDERID","PHASEDESIGNATION","SUBTYPE","CUSTOMERCOUNT","AVGCUSTOMERCONSUMPTION","MAXCUSTOMERCONSUMPTION","STREETADDRESS","eSupportStructure_GLOBALID"]
custAcctFlds = ["GLOBALID","eServicePoint_GlobalID","AVGCONSUMPTION","MAXCONSUMPTION"]

for fldName in arcpy.ListFields(svcPntDest):
    if fldName.name in svcPntFlds:
        print(fldName.name)

In [3]:
if datetime.today().month >= 5 <= 9:
    #print("Using Summer Peak")
    summerPeak = True
    estimatedDemand = {50:2.40,100:2.67,150:2.94,200:3.20,250:3.46,300:3.72,350:3.98,400:4.23,450:4.48,500:4.73,550:4.97,600:5.21,
                    650:5.45,700:5.68,750:5.92,800:6.15,850:6.37,900:6.60,950:6.82,1000:7.03,1050:7.25,1100:7.46,1150:7.67,
                    1200:7.88,1250:8.08,1300:8.28,1350:8.48,1400:8.67,1450:8.86,1500:9.05,1550:9.24,1600:9.42,1650:9.60,
                    1700:9.78,1750:9.95,1800:10.12,1850:10.29,1900:10.46,1950:10.62,2000:10.78,2050:10.94,2100:11.10,2150:11.26,
                    2200:11.41,2250:11.57,2300:11.73,2350:11.89,2400:12.05,2450:12.21,2500:2.36,2550:2.52,2600:12.68,2650:12.84,
                    2700:13.00,2750:13.16,2800:13.31,2850:13.47,2900:13.63,2950:13.79,3000:13.95}
else:
    #print("Using Winter Peak")
    winterPeak = True
    estimatedDemand = {50:1.97,100:2.33,150:2.69,200:3.05,250:3.41,300:3.76,350:4.11,400:4.45,450:4.80,500:5.14,550:5.48,
                       600:5.82,650:6.15,700:6.49,750:6.82,800:7.14,850:7.47,900:7.79,950:8.11,1000:8.43,1050:8.74,1100:9.05,
                       1150:9.36,1200:9.67,1250:9.97,1300:10.27,1350:10.57,1400:10.87,1450:11.16,1500:11.45,1550:11.74,1600:12.03,
                       1650:12.31,1700:12.60,1750:12.87,1800:13.15,1850:13.42,1900:13.70,1950:13.96,2000:14.23,2050:14.45,
                       2100:14.68,2150:14.90,2200:15.13,2250:15.35,2300:15.58,2350:15.80,2400:16.03,2450:16.25,2500:16.48,
                       2550:16.70,2600:16.93,2650:17.15,2700:17.38,2750:17.60,2800:17.83,2850:18.05,2900:18.28,2950:18.50,
                       3000:18.73}


In [4]:
# coincidence factor
cf = {1:1.0,2:0.85,3:0.74,4:0.66,5:0.61,6:0.57,7:0.54,8:0.52,9:0.5,10:0.49,11:0.47,12:0.46,13:0.45,14:0.43,15:0.42,16:0.41,
      17:0.39,18:0.38,19:0.38,20:0.37}

The loop below needs work. Does not process all related meters and related customer accounts, only first found related meter and customer accounts.

Adding [MakeTableView_management()](http://pro.arcgis.com/en/pro-app/tool-reference/data-management/make-table-view.htm) to get count of related meters to manage the issue mentioned above

In [5]:
def getSvcPnts(txGUID,deviceID):
    arcpy.MakeTableView_management (svcPntDest, deviceID, where_clause=f"eTransformerBank_GLOBALID = '{txGUID}'", gdb)
    svcPntCount = int(arcpy.GetCount_management().getOutput(0))
    if svcPntCount = 1:
        with arcpy.da.SearchCursor(svcPntDest,svcPntFlds,f"eTransformerBank_GLOBALID = '{txGUID}'") as svcPnts:
            #print(f'eTransformerBank_GLOBALID = "{txGUID}"')
            for svcPnt in svcPnts:
                #print(f'svcPntGUID {svcPnt[0]}')
                val1,val2,val3 = getCustAcct(svcPnt[0])
                return val1, val2, val3
        return 0,0,0

In [6]:
def getCustAcct(svcPntGUID):
    count = 0
    kwd = []
    kwdSum = 0
    minimumKVA = 0
    _cf = 1
    with arcpy.da.SearchCursor(custAcctDest,custAcctFlds,f"eServicePoint_GlobalID = '{svcPntGUID}'") as custAccts:
        for custAcct in custAccts:
            if custAcct[3] is None:
                pass
            else:
                custAcctCount += 1
                print(f'MaxConsumption {custAcct[3]} and count is {count}')
                kwdVal = getKWD(custAcct[3])
                if kwdVal is None:
                    kwdVal = calcKWD(custAcct[3])
                kwd.append(kwdVal)
                #if count > 1:
                kwdSum = sum(kwd)
                #print(f'Sum of kwd {kwdSum}')
            _cf = getCF(count)
            if kwdSum == 0:
                pass
            elif _cf is None:
                pass
            else:
                minimumKVA = kwdSum*_cf
            print(f'kwdList: {kwd}')
            print(f'Sum of kwd {kwdSum}')
            print(f'_cf {_cf}')
            print(f'Estimated Load: {minimumKVA}kva')
        return kwdSum, _cf, minimumKVA
    return 0,0,0

In [7]:
def getKWD(consumption):
    for key in sorted(estimatedDemand.keys()):
        if consumption <= key:
            #print(key, estimatedDemand[key])
            return estimatedDemand[key]

In [8]:
def calcKWD(consumption):
    if summerPeak:
        print(f'Using Summer Peak')
        return 13.95+0.0025*(consumption-3000)
    if winterPeak:
        print(f'Using Winter Peak')
        return 18.70+0.0027*(consumption-3000)

In [9]:
def getCF(custCount):
    for key in sorted(cf.keys()):
        if custCount == key:
            #print(key, cf[key])
            return cf[key]
        if custCount >= 20:
            return .37

In [10]:
arcpy.env.workspace = gdb
arcpy.env.overwriteOutput = True

In [11]:
tblList = arcpy.ListTables()
for tbl in tblList:
    print(tbl)
    arcpy.Delete_management(tbl)

eCUSTOMERACCOUNT
SAP_INSTALLATION


In [12]:
fdsList = arcpy.ListDatasets()
for fds in fdsList:
    print(fds)
    arcpy.Delete_management(fds)

Electric


In [13]:
arcpy.Copy_management(custAcctSource,custAcctDest)

<Result 'C:\\Users\\friendde\\Documents\\ArcGIS\\Projects\\ReplaceKVA\\ReplaceKVA.gdb\\eCUSTOMERACCOUNT'>

In [14]:
for fld in txAddFlds:
    arcpy.AddField_management(txDest,fld,"DOUBLE")

In [15]:
edit = arcpy.da.Editor(gdb)
edit.startEditing(False, False)
edit.startOperation()

In [16]:
with arcpy.da.SearchCursor(txDest,txFlds) as txpnts:
        for txpnt in txpnts:
            print(f'TXGUID {txpnt[0]}')
            txFld1,txFld2,txFld3 = getSvcPnts(txpnt[0],txpnt[4])
            with arcpy.da.UpdateCursor(txDest,txAddFlds,f"GLOBALID = '{txpnt[0]}'") as uc:
                #print(row)
                for row in uc:
                    row[0] = txFld1
                    row[1] = txFld2
                    row[2] = txFld3
                    uc.updateRow(row)

TXGUID {AABE1886-61B0-44E6-9DF7-D505A10FFCD2}
MaxConsumption 530.0 and count is 1
kwdList: [4.97]
Sum of kwd 4.97
_cf 1.0
Estimated Load: 4.97kva
TXGUID {D2D5169C-A715-46E0-91EE-36D01B04FC2D}
MaxConsumption 1186.0 and count is 1
kwdList: [7.88]
Sum of kwd 7.88
_cf 1.0
Estimated Load: 7.88kva
TXGUID {7CCCBA17-54EF-42AA-9A87-02159ACDA324}
MaxConsumption 1721.0 and count is 1
kwdList: [9.95]
Sum of kwd 9.95
_cf 1.0
Estimated Load: 9.95kva
TXGUID {DFDB886D-DEB4-43BC-8C61-7DBD12C22C2F}
MaxConsumption 2117.0 and count is 1
kwdList: [11.26]
Sum of kwd 11.26
_cf 1.0
Estimated Load: 11.26kva
TXGUID {ADB0EEA9-99B5-476D-9F44-39730CB65611}
MaxConsumption 1728.0 and count is 1
kwdList: [9.95]
Sum of kwd 9.95
_cf 1.0
Estimated Load: 9.95kva
TXGUID {D90B530F-6540-4FDB-8B46-A8D7FA6797A9}
MaxConsumption 820.0 and count is 1
kwdList: [6.37]
Sum of kwd 6.37
_cf 1.0
Estimated Load: 6.37kva
TXGUID {96580859-EB84-482E-8091-45D049F238CE}
TXGUID {6326E11A-40D8-46C2-93AA-AEFA1D9D2DC9}
TXGUID {8834EFC4-ACD1-49E

MaxConsumption 905.0 and count is 1
kwdList: [6.82]
Sum of kwd 6.82
_cf 1.0
Estimated Load: 6.82kva
TXGUID {2E25E30E-F813-41EE-93AC-4EB7AAB603DD}
MaxConsumption 2383.0 and count is 1
kwdList: [12.05]
Sum of kwd 12.05
_cf 1.0
Estimated Load: 12.05kva
TXGUID {BA352537-3A09-47ED-B4E7-B61A726F0199}
MaxConsumption 3005.0 and count is 1
Using Summer Peak
kwdList: [13.962499999999999]
Sum of kwd 13.962499999999999
_cf 1.0
Estimated Load: 13.962499999999999kva
TXGUID {35FFD175-79CB-43AD-8AF4-AB59F0BF3ED5}
MaxConsumption 1522.0 and count is 1
kwdList: [9.24]
Sum of kwd 9.24
_cf 1.0
Estimated Load: 9.24kva
TXGUID {CF450E85-3CF5-4425-A685-92CD8979E16A}
MaxConsumption 1400.0 and count is 1
kwdList: [8.67]
Sum of kwd 8.67
_cf 1.0
Estimated Load: 8.67kva
TXGUID {68D9C5AB-C551-498A-9F30-B7E50481235F}
MaxConsumption 1688.0 and count is 1
kwdList: [9.78]
Sum of kwd 9.78
_cf 1.0
Estimated Load: 9.78kva
TXGUID {C17BC435-B8D6-4130-8526-D31D6ED38E66}
MaxConsumption 268.0 and count is 1
kwdList: [3.72]
Sum 

MaxConsumption 2020.0 and count is 1
kwdList: [10.94]
Sum of kwd 10.94
_cf 1.0
Estimated Load: 10.94kva
TXGUID {FF87D1D7-DED1-4CA6-97D9-8E6C444852F2}
MaxConsumption 1435.0 and count is 1
kwdList: [8.86]
Sum of kwd 8.86
_cf 1.0
Estimated Load: 8.86kva
TXGUID {8CD98747-EEFA-4FB4-8DA7-07E29E83624C}
MaxConsumption 1013.0 and count is 1
kwdList: [7.25]
Sum of kwd 7.25
_cf 1.0
Estimated Load: 7.25kva
TXGUID {D7130FB9-C7C6-4C60-9343-67FF9C10DDF1}
MaxConsumption 2895.0 and count is 1
kwdList: [13.63]
Sum of kwd 13.63
_cf 1.0
Estimated Load: 13.63kva
TXGUID {818067B0-0AB7-4134-A3A3-1C97A5CC1369}
MaxConsumption 1394.0 and count is 1
kwdList: [8.67]
Sum of kwd 8.67
_cf 1.0
Estimated Load: 8.67kva
TXGUID {DCCF7159-4E52-4502-975B-B4DD1E3DDC2A}
MaxConsumption 1562.0 and count is 1
kwdList: [9.42]
Sum of kwd 9.42
_cf 1.0
Estimated Load: 9.42kva
TXGUID {9928BB76-17F2-4FBB-977F-93ABC76EBC82}
MaxConsumption 2105.0 and count is 1
kwdList: [11.26]
Sum of kwd 11.26
_cf 1.0
Estimated Load: 11.26kva
TXGUID {

MaxConsumption 921.0 and count is 1
kwdList: [6.82]
Sum of kwd 6.82
_cf 1.0
Estimated Load: 6.82kva
TXGUID {69E36152-4D64-464F-A50C-435A0FC2AD4F}
MaxConsumption 1523.0 and count is 1
kwdList: [9.24]
Sum of kwd 9.24
_cf 1.0
Estimated Load: 9.24kva
TXGUID {E3ADA76E-D616-4935-9002-11A1B779C842}
MaxConsumption 1237.0 and count is 1
kwdList: [8.08]
Sum of kwd 8.08
_cf 1.0
Estimated Load: 8.08kva
TXGUID {2D6BB647-A321-4AAE-AE28-DE0918137459}
MaxConsumption 4488.0 and count is 1
Using Summer Peak
kwdList: [17.669999999999998]
Sum of kwd 17.669999999999998
_cf 1.0
Estimated Load: 17.669999999999998kva
TXGUID {DBC4A1EB-CFE9-4BAA-942D-A5101B51B29B}
MaxConsumption 1132.0 and count is 1
kwdList: [7.67]
Sum of kwd 7.67
_cf 1.0
Estimated Load: 7.67kva
TXGUID {1A7E09A1-C08B-4215-98E1-B1AD4406B874}
MaxConsumption 1254.0 and count is 1
kwdList: [8.28]
Sum of kwd 8.28
_cf 1.0
Estimated Load: 8.28kva
TXGUID {D2EC43EC-05C3-419F-A597-D91F8188ED10}
MaxConsumption 1624.0 and count is 1
kwdList: [9.6]
Sum of 

MaxConsumption 2367.0 and count is 1
kwdList: [12.05]
Sum of kwd 12.05
_cf 1.0
Estimated Load: 12.05kva
TXGUID {5AA5AF35-36CA-4340-8D49-50AD7518C65A}
MaxConsumption 2901.0 and count is 1
kwdList: [13.79]
Sum of kwd 13.79
_cf 1.0
Estimated Load: 13.79kva
TXGUID {6DA06EF1-E8CA-4EEC-A432-C71E5CF28670}
MaxConsumption 4147.0 and count is 1
Using Summer Peak
kwdList: [16.8175]
Sum of kwd 16.8175
_cf 1.0
Estimated Load: 16.8175kva
TXGUID {5393597B-00A4-414D-93ED-9BECCD02A83A}
MaxConsumption 4172.0 and count is 1
Using Summer Peak
kwdList: [16.88]
Sum of kwd 16.88
_cf 1.0
Estimated Load: 16.88kva
TXGUID {82251878-73BB-46DC-B6EF-379539E7B3A1}
MaxConsumption 6050.0 and count is 1
Using Summer Peak
kwdList: [21.575]
Sum of kwd 21.575
_cf 1.0
Estimated Load: 21.575kva
TXGUID {3C67B5A1-248E-4B4D-8D0B-566E9F21D5CD}
MaxConsumption 4123.0 and count is 1
Using Summer Peak
kwdList: [16.7575]
Sum of kwd 16.7575
_cf 1.0
Estimated Load: 16.7575kva
TXGUID {8546D2CA-611F-46F4-8538-9BCE1DED010F}
MaxConsumptio

...

_cf 0.61
Estimated Load: 19.5383kva
MaxConsumption 779.0 and count is 6
kwdList: [7.46, 6.6, 5.92, 6.6, 5.45, 6.15]
Sum of kwd 38.18
_cf 0.57
Estimated Load: 21.7626kva
MaxConsumption 637.0 and count is 7
kwdList: [7.46, 6.6, 5.92, 6.6, 5.45, 6.15, 5.45]
Sum of kwd 43.63
_cf 0.54
Estimated Load: 23.560200000000002kva
MaxConsumption 1848.0 and count is 8
kwdList: [7.46, 6.6, 5.92, 6.6, 5.45, 6.15, 5.45, 10.29]
Sum of kwd 53.92
_cf 0.52
Estimated Load: 28.038400000000003kva
MaxConsumption 720.0 and count is 9
kwdList: [7.46, 6.6, 5.92, 6.6, 5.45, 6.15, 5.45, 10.29, 5.92]
Sum of kwd 59.84
_cf 0.5
Estimated Load: 29.92kva
MaxConsumption 760.0 and count is 10
kwdList: [7.46, 6.6, 5.92, 6.6, 5.45, 6.15, 5.45, 10.29, 5.92, 6.15]
Sum of kwd 65.99000000000001
_cf 0.49
Estimated Load: 32.335100000000004kva
MaxConsumption 571.0 and count is 11
kwdList: [7.46, 6.6, 5.92, 6.6, 5.45, 6.15, 5.45, 10.29, 5.92, 6.15, 5.21]
Sum of kwd 71.2
_cf 0.47
Estimated Load: 33.464kva
MaxConsumption 1424.0 and cou

_cf 0.52
Estimated Load: 31.5484kva
MaxConsumption 1571.0 and count is 9
kwdList: [7.88, 8.28, 7.46, 7.88, 6.82, 7.67, 6.6, 8.08, 9.42]
Sum of kwd 70.09
_cf 0.5
Estimated Load: 35.045kva
MaxConsumption 1298.0 and count is 10
kwdList: [7.88, 8.28, 7.46, 7.88, 6.82, 7.67, 6.6, 8.08, 9.42, 8.28]
Sum of kwd 78.37
_cf 0.49
Estimated Load: 38.4013kva
MaxConsumption 1356.0 and count is 11
kwdList: [7.88, 8.28, 7.46, 7.88, 6.82, 7.67, 6.6, 8.08, 9.42, 8.28, 8.67]
Sum of kwd 87.04
_cf 0.47
Estimated Load: 40.9088kva
MaxConsumption 1157.0 and count is 12
kwdList: [7.88, 8.28, 7.46, 7.88, 6.82, 7.67, 6.6, 8.08, 9.42, 8.28, 8.67, 7.88]
Sum of kwd 94.92
_cf 0.46
Estimated Load: 43.6632kva
MaxConsumption 1491.0 and count is 13
kwdList: [7.88, 8.28, 7.46, 7.88, 6.82, 7.67, 6.6, 8.08, 9.42, 8.28, 8.67, 7.88, 9.05]
Sum of kwd 103.97
_cf 0.45
Estimated Load: 46.786500000000004kva
MaxConsumption 1169.0 and count is 14
kwdList: [7.88, 8.28, 7.46, 7.88, 6.82, 7.67, 6.6, 8.08, 9.42, 8.28, 8.67, 7.88, 9.05, 

kwdList: [9.24, 10.78, 9.05]
Sum of kwd 29.07
_cf 0.74
Estimated Load: 21.5118kva
MaxConsumption 1479.0 and count is 4
kwdList: [9.24, 10.78, 9.05, 9.05]
Sum of kwd 38.120000000000005
_cf 0.66
Estimated Load: 25.159200000000006kva
MaxConsumption 1479.0 and count is 5
kwdList: [9.24, 10.78, 9.05, 9.05, 9.05]
Sum of kwd 47.17
_cf 0.61
Estimated Load: 28.7737kva
TXGUID {5C5430E8-67FD-4890-94D5-908406679713}
MaxConsumption 1455.0 and count is 1
kwdList: [9.05]
Sum of kwd 9.05
_cf 1.0
Estimated Load: 9.05kva
MaxConsumption 2294.0 and count is 2
kwdList: [9.05, 11.73]
Sum of kwd 20.78
_cf 0.85
Estimated Load: 17.663kva
TXGUID {759F6689-5139-43E1-9E9A-E72072C38549}
MaxConsumption 2113.0 and count is 1
kwdList: [11.26]
Sum of kwd 11.26
_cf 1.0
Estimated Load: 11.26kva
TXGUID {D55E143E-65A3-40CA-B8AE-B102432AE8D2}
MaxConsumption 1279.0 and count is 1
kwdList: [8.28]
Sum of kwd 8.28
_cf 1.0
Estimated Load: 8.28kva
TXGUID {5E8EF154-EB3A-4F62-B6A0-AC293B673CA5}
MaxConsumption 1875.0 and count is 1

TXGUID {002EE98A-03F8-4D7F-B215-919ECF12BDFB}
MaxConsumption 1978.0 and count is 1
kwdList: [10.78]
Sum of kwd 10.78
_cf 1.0
Estimated Load: 10.78kva
TXGUID {8AFC61E6-5525-4FF6-8EC5-8D9B87DCFB46}
kwdList: []
Sum of kwd 0
_cf None
Estimated Load: 0kva
TXGUID {2267A8B5-92C5-4029-8C5E-66CBF6A74FF3}
kwdList: []
Sum of kwd 0
_cf None
Estimated Load: 0kva
TXGUID {D624E899-952F-4155-B607-6F555250BB8A}
kwdList: []
Sum of kwd 0
_cf None
Estimated Load: 0kva
TXGUID {D868EED2-CF3F-4ACC-A9C1-02530DE71A30}
MaxConsumption 563.0 and count is 1
kwdList: [5.21]
Sum of kwd 5.21
_cf 1.0
Estimated Load: 5.21kva
TXGUID {9EDD5893-231B-4192-AF72-70B425CCDAEB}
kwdList: []
Sum of kwd 0
_cf None
Estimated Load: 0kva
TXGUID {DAB93B58-2902-4A92-9606-757CB5D4AC1B}
MaxConsumption 1151.0 and count is 1
kwdList: [7.88]
Sum of kwd 7.88
_cf 1.0
Estimated Load: 7.88kva
TXGUID {6EBD1511-20FF-4BBA-ACDE-BAA54C60D969}
TXGUID {96C90689-C3A4-46CD-A999-B07E2AD69853}
MaxConsumption 7.0 and count is 1
kwdList: [2.4]
Sum of kwd 2

kwdList: [6.6]
Sum of kwd 6.6
_cf 1.0
Estimated Load: 6.6kva
TXGUID {2D1DE825-6511-4DF1-8CFF-DCB2882115E4}
MaxConsumption 1929.0 and count is 1
kwdList: [10.62]
Sum of kwd 10.62
_cf 1.0
Estimated Load: 10.62kva
TXGUID {9B7A3508-D4EE-4D17-9508-808B27AACE13}
TXGUID {5530AEDF-8421-4F5F-97A1-C489DBEEADDB}
TXGUID {4EEB7D11-3AB0-415F-AA91-AB95966CE9B4}
TXGUID {A97E01EA-BF96-47E2-A7B1-B3E9396DC4DE}
TXGUID {BBA172BD-3421-485C-8CDA-117A60322DB9}
TXGUID {2689F275-01CB-4AEC-A8A9-37E67610E357}
MaxConsumption 10564.0 and count is 1
Using Summer Peak
kwdList: [32.86]
Sum of kwd 32.86
_cf 1.0
Estimated Load: 32.86kva
TXGUID {4588ECA7-36B6-4262-A32D-14A9D5F85CCA}
TXGUID {6965C7AD-E156-44B0-8CAD-955CA6E6F4FF}
MaxConsumption 4889.0 and count is 1
Using Summer Peak
kwdList: [18.6725]
Sum of kwd 18.6725
_cf 1.0
Estimated Load: 18.6725kva
TXGUID {6FD4D2EA-4F8B-44D4-9330-4D283A4B38EE}
TXGUID {689C3318-F32C-40F7-95EB-04F9F7B87227}
TXGUID {6CAA4EE9-2F57-48D6-86B8-58172010E74C}
MaxConsumption 52400.0 and count

TXGUID {E290DC22-6AD4-4973-A2D0-215C9B29A5A5}

In [17]:
edit.stopOperation()
edit.stopEditing(True)

### Use numpy and pandas to export to CSV

Use arcpy [```TableToNumPyArray()```](http://pro.arcgis.com/en/pro-app/arcpy/data-access/tabletonumpyarray.htm)
See also [Working with numpy in ArcGIS](http://pro.arcgis.com/en/pro-app/arcpy/get-started/working-with-numpy-in-arcgis.htm)

nparr = arcpy.da.TableToNumPyArray(custAcctDest,custAcctOutFlds,skip_nulls=True)
#nparr = arcpy.da.TableToNumPyArray(custAcctDest,custAcctOutFlds,null_value=-9999)
pdarr = pd.DataFrame(nparr)
pdarr.to_csv(custAcctFile,header=False, index=False)

TODO - write file to \\gruadmin.gru.com\fs\Groups\OMS Replacement Project\Documents for OSII\Customer and Premise Files

Ready new numpy array for consumption analysis

nparr = arcpy.da.TableToNumPyArray(custAcctDest,["SERVICEPOINTOBJECTID","POINT_X","POINT_Y","AVGCONSUMPTION","MAXCONSUMPTION"],skip_nulls=True)

df = pd.DataFrame(nparr)
df.head()

[```gis.features.SpatialDataFrame()```](https://esri.github.io/arcgis-python-api/apidoc/html/arcgis.features.toc.html?highlight=spatialdataframe#arcgis.features.SpatialDataFrame.from_xy)

from arcgis.features import SpatialDataFrame
from arcgis.gis import GIS
from getpass import getpass
from IPython.display import display

sdf = SpatialDataFrame.from_xy(df,"POINT_X","POINT_Y")
gis = GIS(arcpy.GetActivePortalURL(), username=input("Enter User Name "), password=(getpass()))
#gis = GIS()
#portalDesc = arcpy.GetPortalDescription()
# search and list all items owned by connected user
#query=f'owner:{portalDesc["user"]["username"]} AND title:CW BaseMap'
#itemType="Feature Layer"
#sortField="title"
#sortOrder="asc"
# default max__items is 10
#maxItems=100
#m = gis.content.search(query,itemType,sortField,sortOrder,maxItems)

#consumptionLyr = gis.content.import_data(sdf)

m = gis.map('Gainesville,FL')

m.add_layer(sdf,options={"renderer":"ClassedSizeRenderer","field_name":"MAXCONSUMPTION"})

#m.add_layer(consumptionLyr,options={"renderer":"ClassedSizeRenderer","field_name":"MAXCONSUMPTION"})

m